In [2]:
import numpy as np
from Bio import Phylo
from io import StringIO
from scipy.special import comb
from utilities import *

np.random.seed(42)

In [9]:
class GenSimulator():
    """
    Base class that provide simulation for one genom
    population_size_over_time - times when change lambda
    """
    def __init__(self, number_of_descendants: int, 
                 population_size_over_time: list,
                 mutation_rate: int,
                 lambda_distributation: list):
        self.number_of_descendants = number_of_descendants
        self.lambda_distributation = lambda_distributation
        self.population_size_over_time = population_size_over_time
        self.mutation_rate = mutation_rate
        
        self.poisson_rate = number_of_descendants*mutation_rate + comb(number_of_descendants,2)/lambda_distributation[0]
        
        self.current_population = {}
        self.tree = None
        self.table = {}
    
    
    def init_population(self):
        for i in range(self.number_of_descendants):
            name = generate_name()
            while name in self.current_population.keys(): name = generate_name()
            self.current_population[name] = "{}:{}".format(name, '{}')
            
    def do_event(self, event_type, *args):
        if event_type == 'coalescence':
            self.do_coalescence(*args)
        elif event_type == 'mutation':
            self.do_mutation(*args)
        else:
            raise 'Type not in list'
    
    def do_coalescence(self, current_linage_number, t, delta_t):
        #print('coalescence')
        name_1 = np.random.choice(list(self.current_population.keys()))
        name_2 = np.random.choice(list(self.current_population.keys()))
        while name_1 == name_2: name_2 = np.random.choice(list(self.current_population.keys()))
        left = self.current_population.pop(name_1)
        right = self.current_population.pop(name_2)
        new_name = '{}_{}'.format(name_1, name_2)
        new_branch = '(' + left + ',' + right + ')' + new_name
        #print('------')
        #print(new_name)
        #print(new_branch)
        self.current_population[new_name] =  new_branch.format(t, t) + ':{}' # можно менять на delta_t
    
    def do_mutation(self, current_linage_number, t, delta_t):
        #print('mutation')
        position = np.random.uniform()
        while position in self.table.keys(): position = np.random.uniform()
        name = np.random.choice(list(self.current_population.keys()))
        self.table[position] = name
        
    def generate(self):
        self.init_population()
        t = 0
        i = 0
        current_limit = self.population_size_over_time[i]
        current_linage_number = self.number_of_descendants
        
        while current_linage_number > 1:
            #print(len(self.current_population))
            generated_t = np.random.exponential(self.poisson_rate)
            print(generated_t)
            if generated_t > current_limit and i < len(self.population_size_over_time) - 1:
                # Nothing happens in this intervals
                i = i + 1
                t = current_limit
                current_limit = self.population_size_over_time[i]
                self.poisson_rate = current_linage_number*self.mutation_rate + comb(current_linage_number,2)/self.lambda_distributation[i+1]
                continue
            else:
                t = t + generated_t
                # Chose what happens - mutation or coalesent
                s = current_linage_number*self.mutation_rate + comb(current_linage_number,2)/self.lambda_distributation[i+1]
                event_type = np.random.choice(
                    ['mutation', 'coalescence'],
                    p=[current_linage_number*self.mutation_rate/s,
                       (comb(current_linage_number,2)/self.lambda_distributation[i+1])/s]
                )
                self.do_event(event_type, current_linage_number, t, generated_t)
                current_linage_number = len(self.current_population)
                self.poisson_rate = current_linage_number*self.mutation_rate + comb(current_linage_number,2)/self.lambda_distributation[i+1]
        for tree in self.current_population.values():
            self.tree = tree.format(1000)
    
    def __call__(self):
        if self.tree is None:
            raise "Firstly need to be generated"
        return self.tree, self.table
    
    def plot_tree(self):
        handle = StringIO(self.tree)  # parse the newick string
        tree = Phylo.read(handle, "newick")
        matplotlib.rc('font', size=60)
        # set the size of the figure
        fig = plt.figure(figsize=(100, 200), dpi=100)
        # alternatively
        # fig.set_size_inches(10, 20)
        axes = fig.add_subplot(1, 1, 1)
        Phylo.draw(tree, axes=axes)
        return

In [10]:
lam_time = [6,12]
lam = [3,1,3]
mr = 0.25

In [11]:
test = GenSimulator(100, lam_time, mr, lam)
test.generate()
tree_str,mutation = test()

700.7464507317612
1677.2841930529137
4544.780884387548
292.7669973985159
1011.3918218294242
7133.463171610338
1576.9722666309208
100.49433742534877
2132.4973510546542
896.5657246136647
1039.0234614840203
116.7084247449791
423.7458129351122
3118.6738428025747
1811.151315464345
2783.7388997405424
38.310685716990996
2363.324123592097
237.03716690612342
1661.587779486016
1753.3076495267737
3678.165022761149
1.2902182918390148
260.82903434631737
369.5756266954678
72.87386041519024
1009.7915208427578
1183.8144590625996
96.99751846233602
369.4657367534013
1811.973734899995
319.7449664605643
178.49760087558437
951.6254713741718
267.59127917618144
1119.0544577569224
645.7209861103445
123.23871900930752
599.8262806439633
617.7015657756701
852.6337478035197
27.009325977055592
619.7136944014707
384.4215127151494
136.1151262265423
967.8744595623269
273.5526818404449
652.0452966174394
953.5044505205661
229.03731037111336
689.3793832244302
203.79284096019978
108.70904984773696
357.3247130404257
74.28

In [12]:
test.plot_tree()

In [13]:
mutation

{0.6034485933813779: 'Mo3W_cKQN_gZd6_FILm_zOW5_5W86'}